# Merging EB terms-  NLS -  Encyclopaedia Britannica


### Loading the necessary libraries

In [1]:
import yaml
import matplotlib.pyplot as plt
import numpy as np
import collections
import matplotlib as mpl

In [2]:
import pandas as pd
from yaml import safe_load
from pandas.io.json import json_normalize

### Functions

In [3]:
def read_query_results(filename):
    with open('./results_NLS/'+filename, 'r') as f:
        query_results = safe_load(f)
    return query_results


In [4]:
def write_query_results(filename, results):
    with open('./results_NLS/'+filename, 'w') as f:
        documents = yaml.dump(results, f)

In [85]:
def create_dataframe(query_results):
  
    
    for edition in query_results:
        for page in query_results[edition]:
            #print(page[1].keys())
            column_list=list(page[1].keys())
            break
        break
        
    data=[]
    for edition in query_results:
        for page in query_results[edition]:
            try:
                data.append(page[1])
               
            except:
                pass
    df = pd.DataFrame(data, columns = column_list)
    #removing the columns that I dont need 
    df= df.drop(['last_term_in_page', 'model', 'num_articles', 'num_page_words', 'num_text_unit' , 'text_unit', 'type_archive'], axis=1)
    #renaming the page num
    df= df.rename(columns={"text_unit_id": "page_num", "type_page": "type_article"})
    #removing 'Page' from the string
    df["page_num"] = df["page_num"].str.replace("Page", "")
    df["page_num"] = df["page_num"].astype(int)
    df_tmp= df["edition"].str.split("Volume", expand=True)[1].str.split(",", expand=True)
    df["volume"]= df_tmp[0]
    df["letters"] = df_tmp[1]
    df['volume'] = df["volume"].str.replace(" ", "").astype(int)
    df['term'] = df["term"].str.replace("_def", "")
    df['term']= df["term"].str.replace('[^a-zA-Z0-9]', '')
    mask=df["term"].str.isalpha()
    df=df.loc[mask] 
    df['term'] = df['term'].str.upper()
    
    #df['archive'] = df["archive_filename"].str.replace("/ ", "")144133901/
    

    list_editions={"1":["first", "First"], "2":["second", "Second"],\
               "3":["third", "Third"],\
               "4":["fourth", "Fourth"], \
               "5":["fifth","Fifth"], "6":["sixth","Sixth"],\
               "7":["seventh", "Seventh"], "8":["eighth", "Eighth"]} 
    
    for ed in list_editions:
        for ed_versions in list_editions[ed]:
            mask = df["edition"].str.contains(ed_versions)
            df.loc[mask, 'edition_num'] = ed  
    df['edition_num']=df["edition_num"].astype(int)
    a=df["archive_filename"].str.split("/").str[-2]
    df['source_text_file']= a+ "/" + df["source_text_file"]   
    df= df.drop(['edition', 'archive_filename'], axis=1)
    
    
    df = df[["term", "definition", "related_terms", "num_article_words", "header", "page_num", "term_id_in_page", "type_article", "edition_num", "volume", "letters", "year", "title",  "place", "source_text_file"  ]]
    
    df = df[df['term'] != '']
    
    return df

In [86]:
def create_dataframe_from_file(filename):
    with open('./results_NLS/'+filename, 'r') as f:
        query_results = safe_load(f)
    
    df = create_dataframe(query_results)
    return df

In [8]:
def prune_json(json_dict):
    """
    Method that given a JSON object, removes all its empty fields.
    This method simplifies the resultant JSON.
    :param json_dict input JSON file to prune
    :return JSON file removing empty values
    """
    final_dict = {}
    if not (isinstance(json_dict, dict)):
        # Ensure the element provided is a dict
        return json_dict
    else:
        for a, b in json_dict.items():
            if b or isinstance(b, bool):
                if isinstance(b, dict):
                    aux_dict = prune_json(b)
                    if aux_dict:  # Remove empty dicts
                        final_dict[a] = aux_dict
                elif isinstance(b, list):
                    aux_list = list(filter(None, [prune_json(i) for i in b]))
                    if len(aux_list) > 0:  # Remove empty lists
                        final_dict[a] = aux_list
                else:
                    final_dict[a] = b
    return final_dict

In [9]:
def delete_entries(query_results_updated, eliminate_pages):
    new_results={}
    for edition in query_results_updated:
        new_results[edition]=[]
        for page_idx in range(0, len(query_results_updated[edition])):
            if page_idx not in eliminate_pages[edition]:
                new_results[edition].append(query_results_updated[edition][page_idx])
    return new_results

In [10]:
def merge_terms(query_results):
    eliminate_pages={}
    for edition in query_results:
        eliminate_pages[edition]=[]
        page_number_dict={}
        for page_idx in range(0, len(query_results[edition])):
            
            current_page=query_results[edition][page_idx][0]
            if current_page not in page_number_dict:
                page_number_dict[current_page]=page_idx
        
            element = query_results[edition][page_idx][1]
            if "previous_page" in element['term']:
                current_definition= element["definition"]
                previous_page_idx= page_idx -1
                previous_page_number = current_page -1
                num_article_words=element["num_article_words"]
                related_terms=element["related_terms"]
                
                
                prev_elements = query_results[edition][previous_page_idx][1]
                if prev_elements["last_term_in_page"]:
                   
                    prev_elements["definition"]+=current_definition
                    prev_elements["num_article_words"]+=num_article_words
                    prev_elements["related_terms"]+= related_terms
                    prev_number = int(prev_elements['text_unit_id'].split("Page")[1])
                    
                    for prev_articles_idx in range(page_number_dict[prev_number], page_idx):
                       
                        if query_results[edition][prev_articles_idx][0] == prev_number:
                           
                            query_results[edition][prev_articles_idx][1]["num_page_words"]+=num_article_words
                    
                  
                    for update_element_idx in range(page_number_dict[current_page], page_idx+1):
                        if query_results[edition][update_element_idx][0] == current_page:
                            query_results[edition][update_element_idx][1]["num_page_words"]-=num_article_words
                            query_results[edition][update_element_idx][1]["num_articles"]-=1
                    
                
                eliminate_pages[edition].append(page_idx)
              
   
    new_results= delete_entries(query_results, eliminate_pages)
    
    return new_results

## Reading, Merging articles,  and Writing the results in a new file

In [11]:
query_results=read_query_results('results_eb_1_edition')

In [12]:
query_results_updated =merge_terms(query_results)

In [ ]:
write_query_results("results_eb_1_edition_updated", query_results_updated)

## Creating a dataframe from the updated results

Here we have dropped some columns that we dont longer need. 

- definition:           Definition of the article
- edition_num:          1,2,3,4,5,6,7,8
- header:               Header of the page's article                                  
- num_article_words:    Number of words per article
- place:                Place where the volume was edited (e.g. Edinburgh)                                    
- related_terms:        Related articles (see X article)  
- source_text_file:     File Path of the XML file from which the article belongs       
- term:                 Article name                            
- term_id_in_page:      Number of article in the page     
- page_num:                 Page Number
- title:               Title of the Volume
- type_article:            Type of Page [Full Page| Topic| Mix | Articles]                                       
- year:                 Year of the Volume
- volume:               volume (e.g. 1)
- letters:              leters of the volume (A-B)
- edition_num:           1,2,3,4,5,6,7,8


In [87]:
df=create_dataframe(query_results_updated)

In [88]:
df.tail()

term                                         definition  \
29298  ZWEIBRUGGEN  a county of the palatinate of the Rhine, in Ge...   
29299       ZYGOMA                    in anatomy. See Anatomy p. 152.   
29300  ZYGOMATICUS                  in anatomy,. See Anatomy, p. 306,   
29301  ZYGOPHYLLUM  in botany, a gr.nus of the decanoria monogyma ...   
29302   CORRIGENDA  page 132. col. I. !. 2J, 26. at frow the faliv...   

      related_terms  num_article_words      header  page_num  term_id_in_page  \
29298      [SQALVS]                 23      ZoDZYG       857               23   
29299            []                  6      ZoDZYG       857               24   
29300     [ANATOMY]                  6      ZoDZYG       857               25   
29301            []                 48      ZoDZYG       857               26   
29302            []                655  CORRIGENDA       858                0   

      type_article  edition_num  volume letters  year  \
29298      Article            1       3     M-Z  1773   
29299      Article            1       3     M-Z  1773   
29300      Article            1       3     M-Z  1773   
29301      Article            1       3     M-Z  1773   
29302        Topic            1       3     M-Z  1773   

                                                   title   place  \
29298  Encyclopaedia Britannica: or, A dictionary of ...  London   
29299  Encyclopaedia Britannica: or, A dictionary of ...  London   
29300  Encyclopaedia Britannica: or, A dictionary of ...  London   
29301  Encyclopaedia Britannica: or, A dictionary of ...  London   
29302  Encyclopaedia Britannica: or, A dictionary of ...  London   

                                        source_text_file  
29298  nls-data-encyclopaediaBritannica/alto/18837502...  
29299  nls-data-encyclopaediaBritannica/alto/18837502...  
29300  nls-data-encyclopaediaBritannica/alto/18837502...  
29301  nls-data-encyclopaediaBritannica/alto/18837502...  
29302  nls-data-encyclopaediaBritannica/alto/18837503...

In [89]:
df.to_json(r'./results_NLS/results_eb_1_edition_postprocess_dataframe', orient="index") 

## Playing with the DATAFRAME

In [82]:
#df=create_dataframe_from_file("results_eb_1_edition_updated")

### group results by year

In [90]:
df.groupby("year").count()

term  definition  related_terms  num_article_words  header  page_num  \
year                                                                          
1771  14395       14395          14395              14395   14395     14395   
1773  14628       14628          14628              14628   14628     14628   

      term_id_in_page  type_article  edition_num  volume  letters  title  \
year                                                                       
1771            14395         14395        14395   14395    14395  14395   
1773            14628         14628        14628   14628    14628  14628   

      place  source_text_file  
year                           
1771  14395             14395  
1773  14628             14628

### group results by letters

In [91]:
df.groupby("letters").count()

term  definition  related_terms  num_article_words  header  \
letters                                                                
 A-B      8553        8553           8553               8553    8553   
 C-L     10567       10567          10567              10567   10567   
 M-Z      9903        9903           9903               9903    9903   

         page_num  term_id_in_page  type_article  edition_num  volume   year  \
letters                                                                        
 A-B         8553             8553          8553         8553    8553   8553   
 C-L        10567            10567         10567        10567   10567  10567   
 M-Z         9903             9903          9903         9903    9903   9903   

         title  place  source_text_file  
letters                                  
 A-B      8553   8553              8553  
 C-L     10567  10567             10567  
 M-Z      9903   9903              9903

#### group results by letters and years

In [92]:
df.groupby(['year', 'letters'])["letters"].count()

year  letters
1771   A-B       4204
       C-L       5325
       M-Z       4866
1773   A-B       4349
       C-L       5242
       M-Z       5037
Name: letters, dtype: int64

### filter by TERMS : ABACUS

In [93]:
abacus_df= df[df['term'].str.contains("ABACUS")]
abacus_df = abacus_df[abacus_df['year'] == 1771]
abacus_df

term                                         definition  \
27  ABACUS  a table strewed over with dust or sand, upon w...   
28  ABACUS  in architeflure, signifies the superior part o...   
29  ABACUS  is also the name of an ancient instrument for ...   
30  ABACUS  logijlicus, a right-angled triangle, whose sid...   

                       related_terms  num_article_words  \
27                                []                 23   
28                             [FIG]                122   
29  [FIG, NUMBER, EXAMPLE, COUNTERS]                125   
30                                []                 50   

                     header  page_num  term_id_in_page type_article  \
27  EncyclopaediaBritannica        15               20      Article   
28  EncyclopaediaBritannica        15               21      Article   
29                   ABAABB        16                1      Article   
30                   ABAABB        16                2      Article   

    edition_num  volume letters  year  \
27            1       1     A-B  1771   
28            1       1     A-B  1771   
29            1       1     A-B  1771   
30            1       1     A-B  1771   

                                                title      place  \
27  Encyclopaedia Britannica; or, A dictionary of ...  Edinburgh   
28  Encyclopaedia Britannica; or, A dictionary of ...  Edinburgh   
29  Encyclopaedia Britannica; or, A dictionary of ...  Edinburgh   
30  Encyclopaedia Britannica; or, A dictionary of ...  Edinburgh   

                                     source_text_file  
27  nls-data-encyclopaediaBritannica/alto/18808290...  
28  nls-data-encyclopaediaBritannica/alto/18808290...  
29  nls-data-encyclopaediaBritannica/alto/18808291...  
30  nls-data-encyclopaediaBritannica/alto/18808291...

In [94]:
for i in abacus_df["definition"]:
    print ("ABACUS - Definition: %s" %i)
    print("---")

ABACUS - Definition: a table strewed over with dust or sand, upon which the ancient mathematicians drew their figures, It also signified a cupboard, or buffet.
---
ABACUS - Definition: in architeflure, signifies the superior part or member of the capital of a column, and serves as a kind of crowning to both. It was originally intended to represent a square tile covering a basket. The form of the abacus is not the same in all orders: in the Tuscan, Doric, and Ionic, it‘is generally square; but in the Corinthian and Compofite, its four sides are arched ir Avards, and embellilhed in the middle withornament, as a rose or other flower, Scammozzi uses abacus for a concave moulding on the capital of the Tuscan pedefial; and Palladio calls the plinth above the echinus, or boultin, in the Tufean and Doric orders, by the same name. See plate I. fig. i. and
---
ABACUS - Definition: is also the name of an ancient instrument for facilitating operations in arithmetic. It is vadoully contrived. That 

In [118]:
df_by_term=df.groupby(['term', 'year'])["term"].count()
df_by_term["ABACUS"]


year
1771    4
1773    2
Name: term, dtype: int64

In [128]:
df_new=df[['term', 'year', 'definition']]

In [140]:
groups = df[['term', 'year', 'definition']].groupby(['term', 'year'])
for group_key, group_value in groups:
    group = groups.get_group(group_key)
    print(group)
    print("---- Len of this group: %s - group_key %s " %(len(group), group_key))


      term  year                                         definition
1006     A  1771                                    See Alchemilla.
1088     A  1771  gives a—by and “ the investigation of that sur...
3467     A  1771  -Bladder, in physiology. See Air. ^//-Bladders...
7350     A  1771  in London is cieditor to (B) in Paris, value 1...
12753    A  1771  r Y\ C / 7 f C.A ( ^y \ ~^\ \ C' A h \A v m aa...
12754    A  1771  I -w 'i <? ^' 0 IY\, y f‘ 1 A_-A IV^-/Y\< -'/W...
13438    A  1771  /kins may be tawed : but thc-se chiefly used f...
---- Len of this group: 7 - group_key ('A', 1771) 
      term  year                                         definition
21885    A  1773  in London is creditor to (B) in Paris, value t...
25655    A  1773  l class. ' The calix consists of five leaves, ...
27346    A  1773  are petals, hollow m their lower part, but in ...
---- Len of this group: 3 - group_key ('A', 1773) 
      term  year                                         definition
10101   AA  17

14604  ABERBROTHOCK  1773  one of the royal boroughs of Scotland, situate...
---- Len of this group: 1 - group_key ('ABERBROTHOCK', 1773) 
           term  year                                         definition
14605  ABERDEEN  1773  the name of two cities in Scotland, called the...
---- Len of this group: 1 - group_key ('ABERDEEN', 1773) 
           term  year                                         definition
14606  ABERDOUR  1773  a small town in Fifeftrire, Scotland, on the f...
---- Len of this group: 1 - group_key ('ABERDOUR', 1773) 
             term  year                                         definition
14607  ABERGAVENY  1773  in Monmouthfiiire, England, a wellbuilt town, ...
---- Len of this group: 1 - group_key ('ABERGAVENY', 1773) 
             term  year                                         definition
14608  ABERMURDER  1773  an old law-term for murder, proved in a judici...
---- Len of this group: 1 - group_key ('ABERMURDER', 1773) 
             term  year          

         term  year                                         definition
148  ABSCONSA  1771  a dark lanthorn used by the monks at the cerem...
---- Len of this group: 1 - group_key ('ABSCONSA', 1771) 
           term  year                                         definition
14688  ABSCONSA  1773  a dark lanthorn used by the monks at the cerem...
---- Len of this group: 1 - group_key ('ABSCONSA', 1773) 
        term  year                                         definition
149  ABSENCE  1771  in Scots law: When a person cited before a cou...
---- Len of this group: 1 - group_key ('ABSENCE', 1771) 
          term  year                                         definition
14689  ABSENCE  1773  in Scots law: When a person cited before a Cou...
---- Len of this group: 1 - group_key ('ABSENCE', 1773) 
             term  year                                         definition
150  ABSINTHIATED  1771  medicines, such as are impregnated with abfint...
---- Len of this group: 1 - group_key ('ABSINTHI

---- Len of this group: 1 - group_key ('ACARAAYAJ', 1771) 
       term  year                                         definition
231  ACARAI  1771  a town in Paraguay in South America, built by ...
---- Len of this group: 1 - group_key ('ACARAI', 1771) 
         term  year                                         definition
14771  ACARAI  1773  a town in Paraguay in South America, built by ...
---- Len of this group: 1 - group_key ('ACARAI', 1773) 
          term  year                           definition
229  ACARAPEBA  1771  in ichthyology, an ohtolete name of
---- Len of this group: 1 - group_key ('ACARAPEBA', 1771) 
            term  year                                         definition
14769  ACARAPEBA  1773  in ichthyology, an obiolete name of the fparus...
---- Len of this group: 1 - group_key ('ACARAPEBA', 1773) 
            term  year                                         definition
230  ACARAPINIMA  1771  in ichthyology, an obsolete name of the fparus...
---- Len of this gr

14834  ACCOMPAGNAGE  1773  a term in the silk manufadtures, signifying a ...
---- Len of this group: 1 - group_key ('ACCOMPAGNAGE', 1773) 
                term  year                                         definition
14835  ACCOMPANIMENT  1773  some thing attending or added as a circumflanc...
---- Len of this group: 1 - group_key ('ACCOMPANIMENT', 1773) 
          term  year    definition
14837  ACCOMPT  1773  See Account.
---- Len of this group: 1 - group_key ('ACCOMPT', 1773) 
             term  year                                         definition
14838  ACCOMPTANT  1773  See Accountant. ACCORD, in music. See Concord....
---- Len of this group: 1 - group_key ('ACCOMPTANT', 1773) 
           term  year                                         definition
14839  ACCORNED  1773  in heraldry : When any figure of an animal, in...
---- Len of this group: 1 - group_key ('ACCORNED', 1773) 
          term  year                                         definition
14840  ACCOUNT  1773  or Acco

...

               term  year                         definition
26389  PRESCRIPTION  1773  in Scots law. See Law, Tit. xxvi.
---- Len of this group: 1 - group_key ('PRESCRIPTION', 1773) 
           term  year                                         definition
11729  PRESENCE  1771  a term of relation used in opposition to absen...
---- Len of this group: 1 - group_key ('PRESENCE', 1771) 
           term  year                                         definition
26390  PRESENCE  1773  a term of relation used in opposition to absen...
---- Len of this group: 1 - group_key ('PRESENCE', 1773) 
          term  year                      definition
11730  PRESENT  1771  tense, in grammar. See Grammar
---- Len of this group: 1 - group_key ('PRESENT', 1771) 
          term  year                             definition
26391  PRESENT  1773  tsnse, in grammar. See Grammar. FRE-.
---- Len of this group: 1 - group_key ('PRESENT', 1773) 
               term  year                         definition
26392  

11847  PUDENDA  1771  the parts of generation in both sexes. See
---- Len of this group: 1 - group_key ('PUDENDA', 1771) 
          term  year                                  definition
26531  PUDENDA  1773  the parts of generation in both sexes. See
---- Len of this group: 1 - group_key ('PUDENDA', 1773) 
            term  year                                         definition
11848  PUERILITY  1771  in discourse, is defined by Longinus, to be a ...
---- Len of this group: 1 - group_key ('PUERILITY', 1771) 
            term  year                                         definition
26532  PUERILITY  1773  in discourse, is defined by Longinus, to be a ...
---- Len of this group: 1 - group_key ('PUERILITY', 1773) 
        term  year                                         definition
11849  PUGIL  1771  in physic, <bc. such a quantity of flowers, fe...
---- Len of this group: 1 - group_key ('PUGIL', 1771) 
        term  year                                         definition
26533  PUGIL

26598  QUILLS  1773  the large feathers taken out of the end of the...
---- Len of this group: 1 - group_key ('QUILLS', 1773) 
           term  year                                         definition
11915  QUINCUNX  1771  in Roman antiquity, denotes anything that cons...
---- Len of this group: 1 - group_key ('QUINCUNX', 1771) 
           term  year                                         definition
26600  QUINCUNX  1773  in Roman antiquity, denotes anything that cons...
---- Len of this group: 1 - group_key ('QUINCUNX', 1773) 
              term  year                                         definition
11916  QUINDECAGON  1771  in geometry, a plain figure with fifteen sides...
---- Len of this group: 1 - group_key ('QUINDECAGON', 1771) 
              term  year                                         definition
26601  QUINDECAGON  1773  in geometry, a plain figure with fifteen sides...
---- Len of this group: 1 - group_key ('QUINDECAGON', 1773) 
                term  year             

---- Len of this group: 1 - group_key ('RATCH', 1773) 
           term  year                                   definition
11985  RATCHETS  1771  in a watch, are the small teeth at the bot-
---- Len of this group: 1 - group_key ('RATCHETS', 1771) 
           term  year                                         definition
26655  RATCHETS  1773  in a watch, are the fmaii teeth at the bpt-of ...
---- Len of this group: 1 - group_key ('RATCHETS', 1773) 
         term  year                                         definition
26656  RATEEN  1773  in commerce, a thick woollen fluff, quilted, w...
---- Len of this group: 1 - group_key ('RATEEN', 1773) 
               term  year                                         definition
26657  RATIFICATION  1773  an adt approving off, and confirming something...
---- Len of this group: 1 - group_key ('RATIFICATION', 1773) 
        term  year                                         definition
26658  RATIO  1773  in arithmetic and geometry, is that relation 

KeyboardInterrupt: 

In [147]:

#Here we get how many times each term appears per year
g_year_term=df.groupby(['term', 'year']).size().reset_index()
g_year_term

term  year  0
0                A  1771  7
1                A  1773  3
2               AA  1771  2
3               AA  1773  3
4              AAB  1773  1
...            ...   ... ..
27017       ZYGOMA  1771  1
27018       ZYGOMA  1773  1
27019  ZYGOMATICUS  1773  1
27020  ZYGOPHYLLUM  1771  1
27021  ZYGOPHYLLUM  1773  1

[27022 rows x 3 columns]

In [182]:
#here we get if a term appears 1 or in 2 sub_edditions. 
terms_per_ed=g_year_term.groupby(['term']).count()
terms_per_ed

year  0
term                
A               2  2
AA              2  2
AAB             1  1
AABAM           1  1
AACH            1  1
...           ... ..
ZUYDERSEE       2  2
ZWEIBRUGGEN     2  2
ZYGOMA          2  2
ZYGOMATICUS     1  1
ZYGOPHYLLUM     2  2

[16023 rows x 2 columns]

In [183]:
terms_only_once=terms_per_ed[terms_per_ed["year"]<2][0]
terms_only_once

term
AAB               1
AABAM             1
AACH              1
AADE              1
AAHUS             1
                 ..
ZEGILETHRON       1
ZFORTIFICATION    1
ZINC              1
ZPARTVI           1
ZYGOMATICUS       1
Name: 0, Length: 5024, dtype: int64

In [184]:
terms_more_once=terms_per_ed[terms_per_ed["year"]>1][0]
terms_more_once

term
A              2
AA             2
AB             2
ABACUS         2
ABADAN         2
              ..
ZUTPHEN        2
ZUYDERSEE      2
ZWEIBRUGGEN    2
ZYGOMA         2
ZYGOPHYLLUM    2
Name: 0, Length: 10999, dtype: int64

In [185]:
g_year_term.groupby(['year']).size()

year
1771    13351
1773    13671
dtype: int64

In [186]:
df.groupby(['term', 'year']).groups.keys()

dict_keys([('A', 1771), ('A', 1773), ('AA', 1771), ('AA', 1773), ('AAB', 1773), ('AABAM', 1771), ('AACH', 1771), ('AADE', 1771), ('AAHUS', 1771), ('AAIRAM', 1773), ('AAITHMEVTIGK', 1773), ('AAM', 1771), ('AAR', 1771), ('AARSEO', 1771), ('AATTER', 1771), ('AB', 1771), ('AB', 1773), ('ABA', 1771), ('ABAC', 1771), ('ABACATUAIA', 1771), ('ABACH', 1771), ('ABACISCUS', 1771), ('ABACO', 1771), ('ABACOT', 1771), ('ABACRE', 1771), ('ABACTORES', 1771), ('ABACTUS', 1771), ('ABACUS', 1771), ('ABACUS', 1773), ('ABADAN', 1771), ('ABADAN', 1773), ('ABADDON', 1771), ('ABADDON', 1773), ('ABADIR', 1771), ('ABADIR', 1773), ('ABAFT', 1771), ('ABAFT', 1773), ('ABAI', 1771), ('ABAISED', 1771), ('ABAISED', 1773), ('ABAISSE', 1771), ('ABAISSE', 1773), ('ABALIENATION', 1771), ('ABALIENATION', 1773), ('ABANBO', 1771), ('ABANBO', 1773), ('ABANCAI', 1771), ('ABANCAI', 1773), ('ABANO', 1771), ('ABANO', 1773), ('ABAPTISTON', 1771), ('ABAPTISTON', 1773), ('ABARCA', 1771), ('ABARCA', 1773), ('ABARTICULATION', 1771), 

In [187]:
len(df.groupby(['term']).groups['ABACUS'])

6

In [138]:
a=df.groupby(['term', 'year'])['definition'].count()
a

term         year
A            1771    7
             1773    3
AA           1771    2
             1773    3
AAB          1773    1
                    ..
ZYGOMA       1771    1
             1773    1
ZYGOMATICUS  1773    1
ZYGOPHYLLUM  1771    1
             1773    1
Name: definition, Length: 27022, dtype: int64

## Related Terms

In [23]:
import networkx as nx
import matplotlib.pyplot as plt

In [24]:
def create_graph_df(df):

    graph_df = nx.from_pandas_edgelist(df, source='term', target='related_terms', edge_attr=True)
    return graph_df
   

### Selecting the volumes 1771

In [25]:
#select the fist volume of year 1771

df_1771_vol1 = df[(df['year'] == 1771) & (df['volume'] == 1) ]


In [26]:
df_1771_vol1.count()

term                 4250
definition           4250
related_terms        4250
num_article_words    4250
header               4250
page_num             4250
term_id_in_page      4250
type_article         4250
edition_num          4250
volume               4250
letters              4250
year                 4250
title                4250
place                4250
source_text_file     4250
dtype: int64

In [ ]:
df_related_1771_vol1=df_1771_vol1[df_1771_vol1['related_terms'].apply(lambda x: len(x)) > 0]

In [ ]:
df_related_1771_vol1=df_related_1771_vol1.explode('related_terms')

In [ ]:
df_related_1771_vol1

In [ ]:
graph_df = create_graph_df(df_related_1771_vol1)

In [ ]:
plt.figure(figsize=(12,8))
nx.draw_networkx(graph_df, with_labels=True)

In [ ]:
plt.figure(figsize=(15,15))
pos = nx.spring_layout(graph_df)
nx.draw(graph_df, with_labels=True, node_color='skyblue', edge_cmap=plt.cm.Blues, pos = pos)
plt.show()

### Selecting the volumes 1773

In [ ]:
#select the volumes of year 1773
df_1773_vol1 = df[(df['year'] == 1773) & (df['volume'] == 1) ]

In [ ]:
df_1773_vol1.count()

In [ ]:
df_related_1773_vol1=df_1773_vol1[df_1773_vol1['related_terms'].apply(lambda x: len(x)) > 0]

In [ ]:
df_related_1773_vol1=df_related_1773_vol1.explode('related_terms')

In [ ]:
df_related_1773_vol1

In [ ]:
graph_df = create_graph_df(df_related_1773_vol1)

In [ ]:
#plt.figure(figsize=(12,8))
#nx.draw_networkx(graph_df, with_labels=True)

In [ ]:
plt.figure(figsize=(15,15))
pos = nx.spring_layout(graph_df)
nx.draw(graph_df, with_labels=True, node_color='skyblue', edge_cmap=plt.cm.Blues, pos = pos)
plt.show()